In [ ]:
# Import necessary libraries
import pandas as pd
import json
import re
from wordcloud import WordCloud
from nltk.corpus import stopwords
import torch
import base64
from io import BytesIO
import matplotlib.pyplot as plt
from tqdm import tqdm

from transformers import pipeline, AutoTokenizer, AutoModelForSequenceClassification
# Load additional resources if needed
import nltk
nltk.download('stopwords')

# Load the CSV data
# file_path = 'final_labeled_reviews.csv'  # Replace with actual file path or file ID if on Google Cloud
# df = pd.read_csv(file_path)


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [ ]:
#from google.colab import drive
#drive.mount('/content/drive')

In [ ]:
from google.cloud import storage
from google.oauth2 import service_account
import os

def download_blob(bucket_name, source_blob_name, destination_file_name):
    """Downloads a blob from the bucket."""
    SERVICE_ACCOUNT_FILE = 'amplified-brook-416922-6a39d3e05104.json'  # Replace if needed
    credentials = service_account.Credentials.from_service_account_file(
        SERVICE_ACCOUNT_FILE
    )

    storage_client = storage.Client(project='amplified-brook-416922', credentials=credentials)  # Replace project ID if needed
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(source_blob_name)

    blob.download_to_filename(destination_file_name)

    print(
        f"Blob {source_blob_name} downloaded to {destination_file_name}."
    )

# Example usage:
bucket_name = "text-mining-labeled-data"  # Replace with your bucket name
source_blob_name = "final_labeled_reviews"  # Replace with the name of the file in the bucket
destination_file_name = "final_labeled_reviews.csv"  # Replace with the desired local filename

download_blob(bucket_name, source_blob_name, destination_file_name)

file_path = 'final_labeled_reviews.csv'  # Replace with actual file path or file ID if on Google Cloud
df = pd.read_csv(file_path)



Blob final_labeled_reviews downloaded to final_labeled_reviews.csv.


In [ ]:
display(df.head(10))

Index  source  bank                                              title  \
0      0  reddit  CIBC  I just had the worst experience with CIBC, wil...   
1      1  reddit  CIBC         CIBC called and asked "How are you doing?"   
2      2  reddit  CIBC                          What’s so bad about CIBC?   
3      3  reddit  CIBC  Cibc just increased my LOC interest rate by 3....   
4      4  reddit  CIBC                            CIBC closing my account   
5      5  reddit  CIBC  If CIBC is going to charge me $7/mo for the ch...   
6      6  reddit  CIBC  We can put a man on the moon, but it still tak...   
7      7  reddit  CIBC                               CIBC Account Drained   
8      8  reddit  CIBC  Should I close my line of credit with an inter...   
9      9  reddit  CIBC  CIBC has quietly changed its credit score prov...   

                                         review_text  rating  \
0  I helped my dad apply for a CIBC credit card 4...    1515   
1  I'm not sure if this is a fraud call or not. C...     227   
2  It seems from the big 5 banks everyone has som...       0   
3  I’m carrying a fairly large balance on my LOC ...    1088   
4  Received a letter today from CIBC stating they...     750   
5  They're waiving the fee because it's a Youth A...     250   
6  [CIBC policy](https://cibc.intelliresponse.com...    2116   
7  My wife (30F) has been banking with CIBC since...     617   
8  Hello Everyone,\n\nI recently received a $20,0...      95   
9  This is for CIBC's App. \n\n**BEFORE:** Your c...     610   

               date                                                url  \
0  2021-05-22 20:03  https://www.reddit.com/r/PersonalFinanceCanada...   
1  2022-12-07 16:51  https://www.reddit.com/r/PersonalFinanceCanada...   
2   2022-03-15 0:57  https://www.reddit.com/r/PersonalFinanceCanada...   
3  2023-07-19 17:37  https://www.reddit.com/r/PersonalFinanceCanada...   
4  2023-06-25 17:22  https://www.reddit.com/r/PersonalFinanceCanada...   
5  2024-08-15 14:15  https://www.reddit.com/r/PersonalFinanceCanada...   
6  2021-06-04 15:37  https://www.reddit.com/r/PersonalFinanceCanada...   
7  2023-01-25 12:12  https://www.reddit.com/r/PersonalFinanceCanada...   
8   2024-08-23 4:07  https://www.reddit.com/r/PersonalFinanceCanada...   
9  2023-07-20 12:38  https://www.reddit.com/r/PersonalFinanceCanada...   

  source_type                              review_text_processed  \
0        post  helped dad apply cibc credit card week ago onl...   
1        post  sure fraud call cibc randomly called ask neede...   
2        post         seems big bank everyone something cibc bad   
3        post  carrying fairly large balance loc pay anytime ...   
4        post  received letter today cibc stating ending bank...   
5        post  waiving fee youth account start charging mo ch...   
6        post  cibc policy http cibc intelliresponse com publ...   
7        post  wife banking cibc since kid apparently mother ...   
8        post  hello everyone recently received line credit i...   
9        post  cibc app credit score equifax conveniently dis...   

  predicted_sentiment  
0            negative  
1            negative  
2            negative  
3             neutral  
4             neutral  
5             neutral  
6             neutral  
7             neutral  
8             neutral  
9             neutral

In [ ]:
model_name = "cardiffnlp/twitter-roberta-base-sentiment-latest"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(model_name)

def preprocess_text(text, stop_words):
    # Basic preprocessing
    text = re.sub(r'[^\w\s]', '', text.lower())  # Remove punctuation and lowercase
    words = [word for word in text.split() if word not in stop_words]
    return ' '.join(words)

def generate_word_cloud(text, sentiment):
    stop_words = set(stopwords.words('english'))
    custom_stopwords = {"the", "and", "to", "in", "it", "is", "this", "that", "with", "for", "on", "as", "was",
                        "are", "but", "be", "have", "at", "or", "from", "app", "bank", "service", "customer", "one",
                        "like", "can", "get", "use", "using", "also", "would", "will", "make", "good", "bad", "app",
                        "bank", "service", "customer", "one", "like", "can", "get", "use", "using", "also", "would",
                        "will", "make", "still", "even"}
    stop_words.update(custom_stopwords)
    text = preprocess_text(text, stop_words)
    words = re.findall(r'\b\w+\b', text.lower())
    sentiment_words = []
    # Initialize progress bar for word processing
    print("Processing words for sentiment analysis:")
    for word in tqdm(words, desc="Analyzing", unit="word"):
        if word not in stop_words and len(word) > 2:
            # Analyze sentiment of each word using RoBERTa
            inputs = tokenizer(word, return_tensors="pt")
            outputs = model(**inputs)
            scores = torch.softmax(outputs.logits, dim=1).detach().numpy()[0]
            positive_score, neutral_score, negative_score = scores[2], scores[1], scores[0]

            # Filter words based on sentiment
            if sentiment == 'positive' and positive_score > 0.4:
                sentiment_words.append(word)
                print("postive: ",sentiment_words);
            elif sentiment == 'negative' and negative_score > 0.3:
                sentiment_words.append(word)
                print("postive: ",sentiment_words);
    return ' '.join(sentiment_words)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/929 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


pytorch_model.bin:   0%|          | 0.00/501M [00:00<?, ?B/s]

Some weights of the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment-latest were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
def analyze_service_sentiment(df, bank_name):
    result = {
        "bank": bank_name,
        "services": {},
        "overall": {
            "positive_reviews": [],
            "negative_reviews": []
        }
    }

    # Filter reviews by bank
    bank_reviews = df[df['bank'] == bank_name]

    count = 0
    # Process overall bank-level reviews
    for _, row in bank_reviews.iterrows():
        review_text = row['review_text']
        sentiment = row['predicted_sentiment']

        # Append to overall positive or negative reviews
        if sentiment == 'positive':
            if len(result["overall"]["positive_reviews"]) < 50:
              result["overall"]["positive_reviews"].append(review_text)
        elif sentiment == 'negative':
            if len(result["overall"]["negative_reviews"]) < 50:
              result["overall"]["negative_reviews"].append(review_text)

        count += 1
        if count == 500:
          break
    # Process service-level reviews
    services = ["Credit", "Debit", "Fee", "Rates", "Mortgage", "Online banking",
    "Customer Service", "Interest Rates", "Insurance", "Points",
    "Loan", "Interac", "Mobile banking", "Annual Fee", "Performance",
    "Security", "No Fee", "Rewards", "Yield", "Features",
    "Quick Access", "Mobile Deposit", "App Crash"]

    for service in services:
        count = 0
        result["services"][service] = {"positive_reviews": [], "negative_reviews": []}
        filtered_bank_reviews = bank_reviews[bank_reviews['review_text'].str.contains(service, case=False)]

        for _, row in filtered_bank_reviews.iterrows():
            review_text = row['review_text']
            sentiment = row['predicted_sentiment']
            if service.lower() in review_text.lower():
                if sentiment == 'positive':
                    result["services"][service]["positive_reviews"].append(review_text)
                elif sentiment == 'negative':
                    result["services"][service]["negative_reviews"].append(review_text)

            count += 1
            if count == 100:
              break
    return result


In [ ]:
# Initialize JSON storage
output_data = {}
#for bank_name in df['bank'].unique():
#bank_name = "Scotiabank"
bank_name_list = ["CIBC","TD","RBC","Scotiabank","BMO","NBC"]

for bank_name in bank_name_list:
      # Analyze sentiment for each bank
      bank_data = analyze_service_sentiment(df, bank_name)

      # Generate word clouds for each sentiment for overall bank-level reviews
      positive_text = ' '.join(bank_data["overall"]["positive_reviews"])
      negative_text = ' '.join(bank_data["overall"]["negative_reviews"])
      bank_data["overall"]["positive_wordcloud"] = generate_word_cloud(positive_text, 'positive')
      bank_data["overall"]["negative_wordcloud"] = generate_word_cloud(negative_text, 'negative')

      # Generate word clouds for each service-level sentiment
      for service, reviews in bank_data["services"].items():
          positive_text = ' '.join(reviews["positive_reviews"])
          negative_text = ' '.join(reviews["negative_reviews"])
          reviews["positive_wordcloud"] = generate_word_cloud(positive_text, 'positive')
          reviews["negative_wordcloud"] = generate_word_cloud(negative_text, 'negative')

      # Add to the main output data
      output_data[bank_name] = bank_data

# Save the data to JSON
with open("bank_sentiment_data.json", "w") as json_file:
    json.dump(output_data, json_file, indent=4)

Processing words for sentiment analysis:


Analyzing:   3%|▎         | 54/1584 [00:06<02:27, 10.35word/s]

postive:  ['made']


Analyzing:   4%|▎         | 56/1584 [00:06<02:19, 10.96word/s]

postive:  ['made', 'see']


...

Analyzing:  91%|█████████▏| 2060/2253 [03:08<00:17, 11.31word/s]

postive:  ['broken', 'fees', 'garbage', 'error', 'wrong', 'frustrating', 'issues', 'subpar', 'ridiculous', 'dumbest', 'terrible', 'pathetic', 'pathetic', 'horrible', 'unstable', 'atrocious', 'terrible', 'terrible', 'harm', 'responsible', 'garbagex000d', 'desperately', 'useful', 'unreliable', 'rid', 'bads', 'bankingwhy', 'stupid', 'worse', 'poor', 'breaks', 'embarrassed', 'terrible', 'losing', 'pathetic', 'embarrassingly', 'severely', 'poorly', 'confusing', 'fail', 'lazy', 'disconcerting', 'unable', 'unwilling', 'worried', 'lack', 'deposits', 'deposits', 'useless', 'stop', 'garbage', 'negative', 'surprised', 'kermit', 'frustrating', 'bugs', 'crashing', 'depositing', 'disappointing', 'garbage', 'forced', 'useless', 'blind', 'terrible', 'ugly', 'unintuitive', 'idiotic', 'idiotx000d', 'disappointed', 'disgusting', 'awful', 'disappointing', 'worst', 'painful', 'lacks', 'unreliable', 'ugly', 'wrong', 'institutions', 'institutions', 'incomplete', 'deficiencies', 'suffersx000d', 'mean', 'delay

Analyzing:  92%|█████████▏| 2082/2253 [03:10<00:16, 10.12word/s]

postive:  ['broken', 'fees', 'garbage', 'error', 'wrong', 'frustrating', 'issues', 'subpar', 'ridiculous', 'dumbest', 'terrible', 'pathetic', 'pathetic', 'horrible', 'unstable', 'atrocious', 'terrible', 'terrible', 'harm', 'responsible', 'garbagex000d', 'desperately', 'useful', 'unreliable', 'rid', 'bads', 'bankingwhy', 'stupid', 'worse', 'poor', 'breaks', 'embarrassed', 'terrible', 'losing', 'pathetic', 'embarrassingly', 'severely', 'poorly', 'confusing', 'fail', 'lazy', 'disconcerting', 'unable', 'unwilling', 'worried', 'lack', 'deposits', 'deposits', 'useless', 'stop', 'garbage', 'negative', 'surprised', 'kermit', 'frustrating', 'bugs', 'crashing', 'depositing', 'disappointing', 'garbage', 'forced', 'useless', 'blind', 'terrible', 'ugly', 'unintuitive', 'idiotic', 'idiotx000d', 'disappointed', 'disgusting', 'awful', 'disappointing', 'worst', 'painful', 'lacks', 'unreliable', 'ugly', 'wrong', 'institutions', 'institutions', 'incomplete', 'deficiencies', 'suffersx000d', 'mean', 'delay

Analyzing:  93%|█████████▎| 2090/2253 [03:10<00:17,  9.15word/s]

In [ ]:
print(bank_data["overall"]["positive_wordcloud"])

In [ ]:
from google.cloud import storage
from google.oauth2 import service_account
import os
import csv

def upload_blob(bucket_name, source_file_name, destination_blob_name):
    """Uploads a file to the bucket."""
    # The ID of your GCS bucket
    #bucket_name = "text-mining-source-dump"
    # The path to your file to upload
    #source_file_name = "C:\Users\Subhram Satyajeet\OneDrive - University of Windsor\Desktop\Internship Project 2\Review_Dataset_google_apple_net_banking\Dataset\bmo_google_before_2016.csv"
    # The ID of your GCS object
    #destination_blob_name = "bmo_google_before_2016"

    #Setting the service account credentials for authentication
    SERVICE_ACCOUNT_FILE = 'amplified-brook-416922-6a39d3e05104.json' #key file name
    credentials = service_account.Credentials.from_service_account_file(SERVICE_ACCOUNT_FILE) #setting credentials using key file

    storage_client = storage.Client(project='amplified-brook-416922' ,credentials = credentials)
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)

    # Optional: set a generation-match precondition to avoid potential race conditions
    # and data corruptions. The request to upload is aborted if the object's
    # generation number does not match your precondition. For a destination
    # object that does not yet exist, set the if_generation_match precondition to 0.
    # If the destination object already exists in your bucket, set instead a
    # generation-match precondition using its generation number.
    generation_match_precondition = 0

    blob.upload_from_filename(source_file_name, if_generation_match=generation_match_precondition)

    print(
        f"File {source_file_name} uploaded to {destination_blob_name}."
    )

upload_blob('text-mining-labeled-data','bank_sentiment_data.json','bank_sentiment_data')

